
# Quadratic approximations

In this example, we illustrate the use of the :class:`.QuadApprox` plot
on the Sobieski's SSBJ problem.


In [ ]:
from __future__ import annotations

from gemseo import configure_logger
from gemseo import create_discipline
from gemseo import create_scenario
from gemseo.problems.sobieski.core.design_space import SobieskiDesignSpace

## Import
The first step is to import some high-level functions
and a method to get the design space.



In [ ]:
configure_logger()

## Description

The :class:`.QuadApprox` post-processing
performs a quadratic approximation of a given function
from an optimization history
and plot the results as cuts of the approximation.



## Create disciplines
Then, we instantiate the disciplines of the Sobieski's SSBJ problem:
Propulsion, Aerodynamics, Structure and Mission



In [ ]:
disciplines = create_discipline([
    "SobieskiPropulsion",
    "SobieskiAerodynamics",
    "SobieskiStructure",
    "SobieskiMission",
])

## Create design space
We also create the :class:`.SobieskiDesignSpace`.



In [ ]:
design_space = SobieskiDesignSpace()

## Create and execute scenario
The next step is to build an MDO scenario in order to maximize the range,
encoded 'y_4', with respect to the design parameters, while satisfying the
inequality constraints 'g_1', 'g_2' and 'g_3'. We can use the MDF formulation,
the SLSQP optimization algorithm
and a maximum number of iterations equal to 100.



In [ ]:
scenario = create_scenario(
    disciplines,
    "MDF",
    "y_4",
    design_space,
    maximize_objective=True,
)
scenario.set_differentiation_method()
for constraint in ["g_1", "g_2", "g_3"]:
    scenario.add_constraint(constraint, constraint_type="ineq")
scenario.execute({"algo": "SLSQP", "max_iter": 10})

## Post-process scenario
Lastly, we post-process the scenario by means of the :class:`.QuadApprox`
plot which performs a quadratic approximation of a given function
from an optimization history and plot the results as cuts of the
approximation.



.. tip::

   Each post-processing method requires different inputs and offers a variety
   of customization options. Use the high-level function
   :func:`.get_post_processing_options_schema` to print a table with
   the options for any post-processing algorithm.
   Or refer to our dedicated page:
   `gen_post_algos`.



The first plot shows an approximation of the Hessian matrix
$\frac{\partial^2 f}{\partial x_i \partial x_j}$ based on the
*Symmetric Rank 1* method (SR1) :cite:`Nocedal2006`. The
color map uses a symmetric logarithmic (symlog) scale.
This plots the cross influence of the design variables on the objective function
or constraints. For instance, on the last figure, the maximal second-order
sensitivity is $\frac{\partial^2 -y_4}{\partial^2 x_0} = 2.10^5$,
which means that the $x_0$ is the most influential variable. Then,
the cross derivative
$\frac{\partial^2 -y_4}{\partial x_0 \partial x_2} = 5.10^4$
is positive and relatively high compared to the previous one but the combined
effects of $x_0$ and  $x_2$ are non-negligible in comparison.



In [ ]:
scenario.post_process("QuadApprox", function="-y_4", save=False, show=True)

The second plot represents the quadratic approximation of the objective around the
optimal solution : $a_{i}(t)=0.5 (t-x^*_i)^2
\frac{\partial^2 f}{\partial x_i^2} + (t-x^*_i) \frac{\partial
f}{\partial x_i} + f(x^*)$, where $x^*$ is the optimal solution.
This approximation highlights the sensitivity of the :term:`objective function`
with respect to the :term:`design variables`: we notice that the design
variables $x\_1, x\_5, x\_6$ have little influence , whereas
$x\_0, x\_2, x\_9$ have a huge influence on the objective. This
trend is also noted in the diagonal terms of the :term:`Hessian` matrix
$\frac{\partial^2 f}{\partial x_i^2}$.

